In [76]:
import os
import csv
from dotenv import load_dotenv
import mysql.connector
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go

# Extrak Data

In [59]:
# Load values from the .env file
load_dotenv()

def connect_to_mysql():
    try:
        # Create a connection to the database
        connection = mysql.connector.connect(
            host=os.getenv("DB_HOST"),
            port=os.getenv("DB_PORT"),
            user=os.getenv("DB_USER"),
            password=os.getenv("DB_PASSWORD"),
            database=os.getenv("DB_NAME")
        )

        if connection.is_connected():
            print("Connection to MySQL is successful!")
            return connection
    except mysql.connector.Error as error:
        print("Error:", error)
        return None

def fetch_data_from_table(connection, table_name):
    cursor = connection.cursor()
    query = f"SELECT * FROM {table_name}"
    cursor.execute(query)
    rows = cursor.fetchall()
    columns = [desc[0] for desc in cursor.description]
    cursor.close()
    return columns, rows

def save_to_csv(columns, rows, file_path):
    with open(file_path, 'w', newline='', encoding='utf-8') as csvfile:
        csvwriter = csv.writer(csvfile)
        csvwriter.writerow(columns)
        csvwriter.writerows(rows)

def extrak_data():
    # Connect to the database
    connection = connect_to_mysql()
    
    if connection:
        try:
            # Specify the tables you want to extract data from
            table_names = [
                'factinternetsales', 'dimproduct', 'dimcustomer', 'dimtime', 'dimgeography'
                ]
            
            # Extract and save data for each table
            for table_name in table_names:
                columns, rows = fetch_data_from_table(connection, table_name)
                csv_file_path = os.path.join('extrak-data', f'{table_name}.csv')
                save_to_csv(columns, rows, csv_file_path)
                print(f"Data from table '{table_name}' has been saved to '{csv_file_path}'")
        
        finally:
            # Close the connection
            connection.close()

if __name__ == "__main__":
    extrak_data()

Connection to MySQL is successful!
Data from table 'factinternetsales' has been saved to 'extrak-data\factinternetsales.csv'
Data from table 'dimproduct' has been saved to 'extrak-data\dimproduct.csv'
Data from table 'dimcustomer' has been saved to 'extrak-data\dimcustomer.csv'
Data from table 'dimtime' has been saved to 'extrak-data\dimtime.csv'
Data from table 'dimgeography' has been saved to 'extrak-data\dimgeography.csv'


In [92]:
# Load data from CSV files
def load_data(fact_sales_path, product_path, customer_path, geography_path, time_path):
    fact_sales = pd.read_csv(fact_sales_path)
    products = pd.read_csv(product_path)
    customers = pd.read_csv(customer_path)
    geography = pd.read_csv(geography_path)
    time = pd.read_csv(time_path)
    return fact_sales, products, customers, geography, time

# Merge the dataframes into a single comprehensive dataset.
def merge_data(fact_sales, products, customers, geography, time):
    sales_data = fact_sales.merge(products, on='ProductKey')
    sales_data = sales_data.merge(customers, on='CustomerKey')
    sales_data = sales_data.merge(geography, on='GeographyKey')
    sales_data = sales_data.merge(time, left_on='OrderDateKey', right_on='TimeKey')
    return sales_data

In [93]:
# File paths
fact_internet_sales_path = 'extrak-data/factinternetsales.csv'
dim_product_path = 'extrak-data/dimproduct.csv'
dim_customer_path = 'extrak-data/dimcustomer.csv'
dim_geography_path = 'extrak-data/dimgeography.csv'
dim_time_path = 'extrak-data/dimtime.csv'

# Load data
fact_sales, products, customers, geography, time = load_data(fact_internet_sales_path, dim_product_path, dim_customer_path, dim_geography_path, dim_time_path)

# Merge data
sales_data = merge_data(fact_sales, products, customers, geography, time)

# Visualization Sales Analysis

#### Plot a bar chart for the top selling products.

In [85]:
top_products = sales_data.groupby('EnglishProductName')['SalesAmount'].sum().nlargest(10).reset_index()
fig = px.bar(top_products, 
             x='SalesAmount', 
             y='EnglishProductName', 
             orientation='h',  # Horizontal bar chart
             color='SalesAmount', 
             color_continuous_scale='Viridis',
             title='Top 10 Selling Products',
             labels={'EnglishProductName': 'Product', 'SalesAmount': 'Total Sales'},
             template='plotly_dark')
fig.update_traces(texttemplate='%{x:.2s}', textposition='outside')
fig.update_layout(
    xaxis_title='Total Sales',
    yaxis_title='Product',
    showlegend=False,
    xaxis=dict(showgrid=False),
    yaxis=dict(showgrid=False),
    margin=dict(l=100, r=20, t=70, b=70),
    coloraxis_showscale=False
)
top_product = top_products.iloc[0]
fig.add_annotation(x=top_product['SalesAmount'], 
                   y=top_product['EnglishProductName'], 
                   text='Highest Seller', 
                   showarrow=True,
                   arrowhead=2,
                   ax=-70,
                   ay=0,
                   bordercolor='red',
                   borderwidth=2,
                   borderpad=4,
                   bgcolor='white',
                   opacity=0.8)
fig.show()

##### Plot a map showing the sales distribution by city.

In [86]:
sales_by_city = sales_data.groupby('City')['SalesAmount'].sum().reset_index()
sales_by_city['HoverText'] = sales_by_city['City'] + ': $' + sales_by_city['SalesAmount'].astype(str)
fig = px.scatter_geo(sales_by_city, 
                     locationmode='USA-states',
                     locations='City',
                     size='SalesAmount',
                     color='SalesAmount',
                     hover_name='City',
                     hover_data={'SalesAmount': True, 'City': False},
                     text='City',
                     title='Sales Distribution by City',
                     template='plotly_dark',
                     scope='usa',
                     color_continuous_scale=px.colors.sequential.Plasma)
top_cities = sales_by_city.nlargest(5, 'SalesAmount')
for _, row in top_cities.iterrows():
    fig.add_annotation(
        x=row['City'],
        y=row['SalesAmount'],
        text=row['City'] + ": $" + str(row['SalesAmount']),
        showarrow=True,
        arrowhead=1,
        ax=-50,
        ay=-30,
        font=dict(color="white", size=12)
    )
fig.update_geos(
    projection_type="albers usa",
    showland=True, landcolor="lightgray",
    subunitcolor="black"
)
fig.update_layout(
    title_font=dict(size=24, family='Arial', color='white'),
    geo=dict(
        bgcolor='rgba(0,0,0,0)'
    ),
    margin={"r":0,"t":50,"l":0,"b":0}
)
fig.show()

#### Plot a scatter plot showing the relationship between sales amount and quantity sold.

In [94]:
# Plot a scatter plot showing the relationship between sales amount and quantity sold
fig = px.scatter(
    sales_data,
    x='OrderQuantity',
    y='SalesAmount',
    title='Sales vs. Quantity Sold',
    color='ProductLine',  # Assuming ProductLine exists in dimproduct
    size='SalesAmount',
    hover_data=['ProductKey', 'EnglishProductName'],
    labels={
        'OrderQuantity': 'Quantity Sold',
        'SalesAmount': 'Total Sales Amount',
        'ProductLine': 'Product Line'
    },
    template='plotly_dark'
)

# Update layout for better visual appeal
fig.update_layout(
    title_font_size=24,
    xaxis_title_font_size=18,
    yaxis_title_font_size=18,
    legend_title_font_size=16,
    legend=dict(
        x=1,
        y=1,
        title='Product Line',
        bgcolor='rgba(255,255,255,0.5)',
        bordercolor='black',
        borderwidth=1
    ),
    margin=dict(l=50, r=50, t=50, b=50)
)

# Update marker style for better visibility
fig.update_traces(marker=dict(line=dict(width=1, color='DarkSlateGrey')))

# Show the plot
fig.show()

In [79]:
def plot_sales_vs_quantity(sales_data):
    fig = px.scatter(sales_data, x='Quantity', y='SalesAmount', title='Sales vs. Quantity Sold')
    fig.show()

# Plot a donut chart showing the sales composition by product category.
def plot_sales_composition_donut(sales_data):
    sales_by_category = sales_data.groupby('ProductCategory')['SalesAmount'].sum().reset_index()
    fig = px.pie(sales_by_category, names='ProductCategory', values='SalesAmount', title='Sales Composition by Product Category', hole=0.3)
    fig.show()

# Plot a stacked column chart showing monthly sales composition by product category.
def plot_monthly_sales_composition(sales_data):
    monthly_sales = sales_data.groupby(['CalendarYear', 'MonthNumberOfYear', 'ProductCategory'])['SalesAmount'].sum().reset_index()
    fig = px.bar(monthly_sales, x='MonthNumberOfYear', y='SalesAmount', color='ProductCategory', title='Monthly Sales Composition', barmode='stack')
    fig.show()

# Plot a line histogram showing the distribution of sales over time.
def plot_sales_distribution_over_time(sales_data):
    sales_over_time = sales_data.groupby('FullDateAlternateKey')['SalesAmount'].sum().reset_index()
    fig = px.line(sales_over_time, x='FullDateAlternateKey', y='SalesAmount', title='Sales Distribution Over Time')
    fig.show()

def main():
    # File paths
    fact_internet_sales_path = 'extrak-data/factinternetsales.csv'
    dim_product_path = 'extrak-data/dimproduct.csv'
    dim_customer_path = 'extrak-data/dimcustomer.csv'
    dim_geography_path = 'extrak-data/dimgeography.csv'
    dim_time_path = 'extrak-data/dimtime.csv'
    
    
    # Load data
    fact_sales, products, customers, geography, time = load_data(fact_internet_sales_path, dim_product_path, dim_customer_path, dim_geography_path, dim_time_path)
    
    # Merge data
    sales_data = merge_data(fact_sales, products, customers, geography, time)
    
    # Generate visualizations
    plot_top_selling_products(sales_data)
    plot_sales_distribution_by_city(sales_data)
    plot_sales_vs_quantity(sales_data)
    plot_sales_composition_donut(sales_data)
    plot_monthly_sales_composition(sales_data)
    plot_sales_distribution_over_time(sales_data)

if __name__ == "__main__":
    main()

ValueError: Value of 'x' is not the name of a column in 'data_frame'. Expected one of ['ProductKey', 'OrderDateKey', 'DueDateKey', 'ShipDateKey', 'CustomerKey', 'PromotionKey', 'CurrencyKey', 'SalesTerritoryKey_x', 'SalesOrderNumber', 'SalesOrderLineNumber', 'RevisionNumber', 'OrderQuantity', 'UnitPrice', 'ExtendedAmount', 'UnitPriceDiscountPct', 'DiscountAmount', 'ProductStandardCost', 'TotalProductCost', 'SalesAmount', 'TaxAmt', 'Freight', 'CarrierTrackingNumber', 'CustomerPONumber', 'ProductAlternateKey', 'ProductSubcategoryKey', 'WeightUnitMeasureCode', 'SizeUnitMeasureCode', 'EnglishProductName', 'StandardCost', 'FinishedGoodsFlag', 'Color', 'SafetyStockLevel', 'ReorderPoint', 'ListPrice', 'SizeActual', 'SizeRange', 'Weight', 'DaysToManufacture', 'ProductLine', 'DealerPrice', 'Class', 'Style', 'ModelName', 'EnglishDescription', 'StartDate', 'EndDate', 'Status', 'GeographyKey', 'CustomerAlternateKey', 'Title', 'FirstName', 'MiddleName', 'LastName', 'NameStyle', 'BirthDate', 'Marita